# Movie Hit/Flop Classification Using Decision Tree

In this project, we use the TMDB movies dataset to train a Decision Tree Classifier using only pre-release information (like budget, popularity, etc.) to predict whether a movie will be a **Hit** (profitable) or **Flop** (not profitable).


## Step 1: Import Required Libraries

We start by importing the libraries needed for data handling, modeling, and visualization.


In [2]:
# For Data handling and visualization
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# Scikit-learn modules for modeling and evaluation
from sklearn.tree import DecisionTreeClassifier, plot_tree
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report



## Step 2: Load and Clean the Dataset

We load the TMDB dataset and drop irrelevant or text-heavy columns. We also handle missing values in key fields.


In [3]:
# Loading the TMDB movie dataset
df = pd.read_csv('tmdb_movies.csv')

# Droppping irrelevant or text-heavy columns
df.drop(['id', 
         'homepage', 
         'tagline', 
         'original_title', 
         'status', 
         'overview'], axis=1, inplace=True)

# Removing rows with missing release_date
df = df.dropna(subset=['release_date'])

# Filling the missing runtime with the median runtime
df['runtime'] = df['runtime'].fillna(df['runtime'].median())


## Step 3: Filter Valid Movies and Create Labels

We only keep movies with valid budget and revenue. Then we label each movie as:
- **Hit (1)** if ROI > 1
- **Flop (0)** otherwise


In [4]:
# Keep only movies with valid budget and revenue
df = df[(df['budget'] > 0) & (df['revenue'] > 0)].copy()

# Compute ROI (return on investment)
df['ROI'] = df['revenue'] / df['budget'].replace(0, 1)

# Create a binary label: 1 for Hit (ROI > 1), 0 for Flop
df['label'] = (df['ROI'] > 1).astype(int)



## Step 4: Feature Engineering

We extract numerical features that are available before a movie is released (no revenue or ROI used for prediction).


In [5]:
# Extractng release year from release_date
df['release_year'] = pd.to_datetime(df['release_date']).dt.year

# Count the number of genres
df['genre_count'] = df['genres'].apply(lambda x: x.count('{') if pd.notnull(x) else 0)

# Count the number of keywords
df['keyword_count'] = df['keywords'].apply(lambda x: x.count('{') if pd.notnull(x) else 0)

# Count the number of production companies
df['company_count'] = df['production_companies'].apply(lambda x: x.count('{') if pd.notnull(x) else 0)


## Step 5: Define Features and Target

We define:
- `X`: input features available pre-release
- `y`: target label (1 = Hit, 0 = Flop)


In [6]:
# Defineng input features (pre-release only — no revenue/ROI)
features = ['budget', 'popularity', 'runtime', 'vote_average', 'vote_count',
            'genre_count', 'keyword_count', 'company_count']

# Selecting clean feature rows (drop inf/nan)
X = df[features].replace([float('inf'), -float('inf')], pd.NA).dropna()

# Defining target variable (Hit = 1, Flop = 0)
y = df.loc[X.index, 'label']


## Step 6: Train-Test Split

We split the data into training and testing sets to evaluate model performance.


In [7]:
# Split data into 80% train and 20% test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)



## Step 7: Train the Decision Tree Classifier

We train a shallow decision tree for interpretability.


In [8]:
# Initialize and train the Decision Tree
model = DecisionTreeClassifier(criterion='entropy', max_depth=6, random_state=42)
model.fit(X_train, y_train)


DecisionTreeClassifier(criterion='entropy', max_depth=6, random_state=42)

## Step 8: Evaluate Model Performance

We measure accuracy and view precision, recall, and F1-score using a classification report.


In [9]:
# Predict on test data
y_pred = model.predict(X_test)

# Print accuracy
print("Accuracy:", accuracy_score(y_test, y_pred))

# Print precision, recall, F1-score
print("\nClassification Report:\n", classification_report(y_test, y_pred))


Accuracy: 0.781733746130031

Classification Report:
               precision    recall  f1-score   support

           0       0.56      0.46      0.51       157
           1       0.84      0.89      0.86       489

    accuracy                           0.78       646
   macro avg       0.70      0.67      0.68       646
weighted avg       0.77      0.78      0.77       646



## Step 9: Visualize the Decision Tree

We visualize how the model is making predictions using a colored decision tree diagram.


In [29]:
# Plot the decision tree with feature names and class labels
plt.figure(figsize=(170, 100))
plot_tree(model, feature_names=features, class_names=['Flop', 'Hit'], filled=True, rounded=True, fontsize=50)
plt.title("Decision Tree - Movie Hit/Flop Classifier")
plt.show()


## Step 10 Predict From CSV Row Index

In [ ]:

movie_index = 123  # Example: any valid index
movie_row = df.loc[movie_index, features]
movie_df = pd.DataFrame([movie_row])
index_prediction = model.predict(movie_df)[0]
print(f"Movie at index {movie_index} is predicted as:", "Hit" if index_prediction == 1 else "Flop")

Movie at index 123 is predicted as: Hit


In [36]:
movie_index = 173  # Example: any valid index
movie_row = df.loc[movie_index, features]
movie_df = pd.DataFrame([movie_row])
index_prediction = model.predict(movie_df)[0]
print(f"Movie at index {movie_index} is predicted as:", "Hit" if index_prediction == 1 else "Flop")

Movie at index 173 is predicted as: Flop


## Step 11: Predict a New Movie (Before Release)

We test the model by making a prediction for a new, hypothetical movie.


In [11]:
# Define a new movie with only pre-release info
new_movie = pd.DataFrame([{
    'budget': 300000000,         # Production cost: High (300 million)
    'popularity': 4.5,          # Hype: Low
    'runtime': 180,             # Runtime: Long 
    'vote_average': 4.8,        # Rating: Good
    'vote_count': 50,           # Low vote count i.e. less popular among critics
    'genre_count': 3,           
    'keyword_count': 5,         
    'company_count': 2          
}])

# Make prediction
prediction = model.predict(new_movie)[0]
print("Prediction for New Movie:", "Hit" if prediction == 1 else "Flop")



Prediction for New Movie: Flop


In [12]:
new_movie = pd.DataFrame([{
    'budget': 500000000,  # Production cost: High (500 million)
    'popularity': 10.5,   # Hype: High
    'runtime': 120,       # Runtime: Optimal
    'vote_average': 8.8,  # Early rating: High
    'vote_count': 500,    # High vote count i.e. more popular among critics
    'genre_count': 3,
    'keyword_count': 5,
    'company_count': 2
}])

prediction = model.predict(new_movie)[0]
print("Prediction for New Movie:", "Hit" if prediction == 1 else "Flop")


Prediction for New Movie: Hit
